<font color='red' size=5><b>Intital Testing</b></font>

In [3]:
import tensorflow as tf

### In this notebook I followed the example in:

https://www.nengo.ai/nengo-dl/examples/lmu.html

In [2]:
%matplotlib inline

from urllib.request import urlretrieve

import matplotlib.pyplot as plt
import nengo
from nengo.utils.filter_design import cont2discrete
import numpy as np
import tensorflow as tf

import nengo_dl

In [4]:
class LMUCell(nengo.Network):
    def __init__(self, units, order, theta, input_d, **kwargs):
        super().__init__(**kwargs)

        # compute the A and B matrices according to the LMU's mathematical derivation
        # (see the paper for details)
        Q = np.arange(order, dtype=np.float64)
        R = (2 * Q + 1)[:, None] / theta
        j, i = np.meshgrid(Q, Q)

        A = np.where(i < j, -1, (-1.0) ** (i - j + 1)) * R
        B = (-1.0) ** Q[:, None] * R
        C = np.ones((1, order))
        D = np.zeros((1,))

        A, B, _, _, _ = cont2discrete((A, B, C, D), dt=1.0, method="zoh")

        with self:
            nengo_dl.configure_settings(trainable=None)

            # create objects corresponding to the x/u/m/h variables in the above diagram
            self.x = nengo.Node(size_in=input_d)
            self.u = nengo.Node(size_in=1)
            self.m = nengo.Node(size_in=order)
            self.h = nengo_dl.TensorNode(tf.nn.tanh, shape_in=(units,), pass_time=False)

            # compute u_t from the above diagram. we have removed e_h and e_m as they
            # are not needed in this task.
            nengo.Connection(
                self.x, self.u, transform=np.ones((1, input_d)), synapse=None
            )

            # compute m_t
            # in this implementation we'll make A and B non-trainable, but they
            # could also be optimized in the same way as the other parameters.
            # note that setting synapse=0 (versus synapse=None) adds a one-timestep
            # delay, so we can think of any connections with synapse=0 as representing
            # value_{t-1}.
            conn_A = nengo.Connection(self.m, self.m, transform=A, synapse=0)
            self.config[conn_A].trainable = False
            conn_B = nengo.Connection(self.u, self.m, transform=B, synapse=None)
            self.config[conn_B].trainable = False

            # compute h_t
            nengo.Connection(
                self.x, self.h, transform=nengo_dl.dists.Glorot(), synapse=None
            )
            nengo.Connection(
                self.h, self.h, transform=nengo_dl.dists.Glorot(), synapse=0
            )
            nengo.Connection(
                self.m,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=None,
            )

### Example With Dummy data from:
https://machinelearningmastery.com/how-to-develop-convolutional-neural-network-models-for-time-series-forecasting/
 


In [145]:
import nengo
import tensorflow as tf
import numpy as np
import nengo_dl
import matplotlib.pyplot as plt
n_steps = 3
x_train = np.array([[[10, 15], [20, 25], [30, 35]],
                    [[20, 25], [30, 35], [40, 45]],
                    [[30, 35], [40, 45], [50, 55]],
                    [[40, 45], [50, 55], [60, 65]],
                    [[50, 55], [60, 65], [70, 75]],
                    [[60, 65], [70, 75], [80, 85]],
                    [[70, 75], [80, 85], [90, 95]]])
print(x_train.shape)
n_features = x_train.shape[2]
y_train = np.array([[[65]], [[85]], [[105]], [[125]], [[145]], [[165]], [[185]]])
x_test = np.array([[[80, 85], [90, 95], [100, 105]]])
y_test = np.array([[206.0161]])

print(x_test.shape)

with nengo.Network() as net:
    # remove some unnecessary features to speed up the training
    nengo_dl.configure_settings(
        trainable=None,
        stateful=None,
        keep_history=True,
    )

    inp = nengo.Node((np.zeros(x_train.shape[-1])))
    # lmu cell
    lmu = LMUCell(
        units=256,
        order=256,
        theta=x_train.shape[1],
        input_d=x_train.shape[-1],
    )
    

    conn = nengo.Connection(inp, lmu.x, synapse=None)
    net.config[conn].trainable = True    
    
    
 
    # dense linear readout 
    out = nengo.Node(size_in=1) #changed to 1
    nengo.Connection(lmu.h, out,transform=nengo_dl.dists.Glorot(), synapse=None)
   
    p = nengo.Probe(out)   

    
with nengo_dl.Simulator(net) as sim:
    sim.compile(
        loss=tf.losses.mse,
        optimizer=tf.optimizers.Adam(),
#         metrics=["mse"],
    )

    sim.fit(x_train, y_train, epochs=1000)
#     sim.save_params("./lmu_params")
    print(sim.predict(x_test))


(7, 3, 2)
(1, 3, 2)
Build finished in 0:00:00                                                      
Optimization finished in 0:00:00                                               
Construction finished in 0:00:00                                               
Epoch 1/1000
7/7 [==============================] - 2s 5ms/step - loss: 16762.8945 - probe_loss: 16762.8945
Epoch 2/1000
7/7 [==============================] - 0s 5ms/step - loss: 15475.7334 - probe_loss: 15475.7334
Epoch 3/1000
7/7 [==============================] - 0s 5ms/step - loss: 14568.8545 - probe_loss: 14568.8545
Epoch 4/1000
7/7 [==============================] - 0s 5ms/step - loss: 13965.1299 - probe_loss: 13965.1299
Epoch 5/1000
7/7 [==============================] - 0s 6ms/step - loss: 13417.4346 - probe_loss: 13417.4346
Epoch 6/1000
7/7 [==============================] - 0s 5ms/step - loss: 12868.0205 - probe_loss: 12868.0205
Epoch 7/1000
7/7 [==============================] - 0s 5ms/step - loss: 12383.3760 - probe_l

<font color='red' size=5><b>Real Data</b></font>

Now I will try to use the LMU model on S&P500 time series data
I will only select a subsample of the data to train
When I run on the real data model predicts the same value for all samples

In [140]:
from datetime import datetime
import yfinance as yf
import pandas_datareader.data as pdr
import pandas as pd
import numpy as np
from numpy import array


df = data = pd.read_csv("https://raw.githubusercontent.com/Mizanur55/Data/main/S%26P500%20jan1990-jan2021%20%20OHLC%20-%20without%20index.csv")
df

Date         High          Low         Open        Close  \
0     02/01/1990   359.690002   351.980011   353.399994   359.690002   
1     03/01/1990   360.589996   357.890015   359.690002   358.760010   
2     04/01/1990   358.760010   352.890015   358.760010   355.670013   
3     05/01/1990   355.670013   351.350006   355.670013   352.200012   
4     08/01/1990   354.239990   350.540008   352.200012   353.790008   
...          ...          ...          ...          ...          ...   
7807  24/12/2020  3703.820068  3689.320068  3694.030029  3703.060059   
7808  28/12/2020  3740.510010  3723.030029  3723.030029  3735.360107   
7809  29/12/2020  3756.120117  3723.310059  3750.010010  3727.040039   
7810  30/12/2020  3744.629883  3730.209961  3736.189941  3732.040039   
7811  31/12/2020  3760.199951  3726.879883  3733.270020  3756.070068   

          Volume    Adj Close  
0      162070000   359.690002  
1      192330000   358.760010  
2      177000000   355.670013  
3      158530000   352.200012  
4      140110000   353.790008  
...          ...          ...  
7807  1885090000  3703.060059  
7808  3527460000  3735.360107  
7809  3387030000  3727.040039  
7810  3145200000  3732.040039  
7811  3172510000  3756.070068  

[7812 rows x 7 columns]

In [141]:

# split a multivariate sequence into samples
def split_sequences(sequences, n_steps):
    X, y = list(), list()
    for i in range(len(sequences)):
        # find the end of this pattern
        end_ix = i + n_steps
        # check if we are beyond the dataset
        if end_ix > len(sequences):
            break
        # gather input and output parts of the pattern
        seq_x, seq_y = sequences[i:end_ix, :-1], sequences[end_ix-1, -1]
        X.append(seq_x)
        y.append(seq_y)
    return array(X), array(y)

df1 = df[['Open','High','Low','Adj Close']]

# normalizing the dataframe. values are now between [0,1]
# https://stackoverflow.com/questions/26414913/normalize-columns-of-pandas-data-frame

# df1 = (df1-df1.min())/(df1.max()-df1.min())


# gettting all the colums as arrays
open_col = array(df1['Open'])
high_col = array(df1['High'])
low_col = array(df1['Low'])
adj_close_col = array(df1['Adj Close'])
# reshaping the columns
open_col = open_col.reshape(len(open_col),1)
high_col = high_col.reshape(len(high_col),1)
low_col = low_col.reshape(len(low_col),1)
adj_close_col = adj_close_col.reshape(len(adj_close_col),1)
# horizontal staking
dataset = np.hstack((high_col, low_col,adj_close_col))
n_steps = 3
#  X and y have full data - miz
X, y = split_sequences(dataset, n_steps)
# for i in range(len(X)):
#     print(X[i], y[i])

In [142]:
import nengo
import tensorflow as tf
import numpy as np
import nengo_dl
import matplotlib.pyplot as plt
from numpy import array

n_steps = 3
x_train = X[5000:5830]

print(x_train.shape)
n_features = x_train.shape[2]


y_train = y[5000:5830]
#  convering y_train to 3D array
list_of_y = []
for i in y_train:
    list_of_y.append([[i]])
    
y_train = np.array(list_of_y)


x_test = X[5900:5901]
y_test = y[5900:5901]

print(x_test.shape)

with nengo.Network() as net:
    # remove some unnecessary features to speed up the training
    nengo_dl.configure_settings(
        trainable=None,
        stateful=None,
        keep_history=False,
    )

    inp = nengo.Node((np.zeros(x_train.shape[-1])))
    # lmu cell
#      chose these values because they give the best results
    lmu = LMUCell(
        units=516,
        order=516,
        theta=x_train.shape[1],
        input_d=x_train.shape[-1],
    )
    

    conn = nengo.Connection(inp, lmu.x, synapse=None)
    net.config[conn].trainable = False    
    
    
 
    # dense linear readout 
    out = nengo.Node(size_in=1) #changed to 1
    nengo.Connection(lmu.h, out,transform=nengo_dl.dists.Glorot(), synapse=None)
   
    p = nengo.Probe(out)   

    
with nengo_dl.Simulator(net) as sim:
    sim.compile(
        loss=tf.losses.mse,
        optimizer=tf.optimizers.Adam(),
#         metrics=["mse"],
    )
#  I kept the epoch to 10 since the loss does not go down much after that.
    sim.fit(x_train, y_train, epochs=10)
#     sim.save_params("./lmu_params")
    print(sim.predict(x_test))
#     lets print out some different samples to check the output for them
    print(sim.predict(array([X[50]])))
    print(sim.predict(array([X[1000]])))
    print(sim.predict(array([X[2000]])))



(830, 3, 2)
(1, 3, 2)
Build finished in 0:00:00                                                      
Optimization finished in 0:00:00                                               
|             Constructing graph: build stage (0%)             | ETA:  --:--:--

C:\Users\mizan\anaconda3\lib\site-packages\nengo_dl\simulator.py:461: UserWarning: No GPU support detected. See https://www.nengo.ai/nengo-dl/installation.html#installing-tensorflow for instructions on setting up TensorFlow with GPU support.
  "No GPU support detected. See "


Construction finished in 0:00:00                                               
Epoch 1/10
830/830 [==============================] - 10s 9ms/step - loss: 1152515.3750 - probe_loss: 1152515.3750
Epoch 2/10
830/830 [==============================] - 7s 9ms/step - loss: 517001.0625 - probe_loss: 517001.0625
Epoch 3/10
830/830 [==============================] - 7s 9ms/step - loss: 192954.3906 - probe_loss: 192954.3906
Epoch 4/10
830/830 [==============================] - 7s 8ms/step - loss: 59259.9727 - probe_loss: 59259.9727
Epoch 5/10
830/830 [==============================] - 7s 8ms/step - loss: 21344.4512 - probe_loss: 21344.4512
Epoch 6/10
830/830 [==============================] - 8s 9ms/step - loss: 15410.5732 - probe_loss: 15410.5732
Epoch 7/10
830/830 [==============================] - 7s 9ms/step - loss: 15077.1152 - probe_loss: 15077.1152
Epoch 8/10
830/830 [==============================] - 8s 9ms/step - loss: 15084.2217 - probe_loss: 15084.2217
Epoch 9/10
830/830 [===========